# SQL Notebook for SQL Server 2022 data virtualization for parquet files on S3 compatible object storage

This is a SQL notebook to show the data virtualization capabilities in SQL Server 2022 for parquet files on S3 compatible object storage. This notebook is intended for viewing only. However, steps in this notebook can be executed as part of Exercise 5.4 of the SQL Server 2022 workshop at [https://aka.ms/sql2022workshop](https://aka.ms/sql2022workshop).

# Step 1 - Master Key

Create a master key to protect the database scoped credential. Edit the following statement to put in a strong password

In [7]:
USE [WideWorldImporters]
GO
IF NOT EXISTS (SELECT * FROM sys.symmetric_keys WHERE name = '##MS_DatabaseMasterKey##')
	CREATE MASTER KEY ENCRYPTION BY PASSWORD = '<password>';
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.057

# Step 2 - Database Scoped Credential

Create a database scoped credential. Edit the following statement to put in the user and password from RootUser and RootPwd from minio

In [9]:
USE [WideWorldImporters];
GO
-- Have to drop the data source first if it exists
IF EXISTS (SELECT * FROM sys.external_data_sources WHERE name = 's3_wwi')
	DROP EXTERNAL DATA SOURCE s3_wwi;
IF EXISTS (SELECT * FROM sys.database_scoped_credentials WHERE name = 's3_wwi_cred')
    DROP DATABASE SCOPED CREDENTIAL s3_wwi_cred;
GO
CREATE DATABASE SCOPED CREDENTIAL s3_wwi_cred
WITH IDENTITY = 'S3 Access Key',
SECRET = '<user>:<password>';
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.008

# Step 3 - External Data Source

Create an external data source. Edit the script to put in your local IP address

In [10]:
USE [WideWorldImporters];
GO
IF EXISTS (SELECT * FROM sys.external_data_sources WHERE name = 's3_wwi')
	DROP EXTERNAL DATA SOURCE s3_wwi;
GO
CREATE EXTERNAL DATA SOURCE s3_wwi
WITH
(
 LOCATION = 's3://<local IP>:9000'
,CREDENTIAL = s3_wwi_cred
);
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.006

# Step 4 - External file format

Create an external format file for parquet to be used for external tables

In [11]:
USE [WideWorldImporters];
GO
IF EXISTS (SELECT * FROM sys.external_file_formats WHERE name = 'ParquetFileFormat')
	DROP EXTERNAL FILE FORMAT ParquetFileFormat;
CREATE EXTERNAL FILE FORMAT ParquetFileFormat WITH(FORMAT_TYPE = PARQUET);
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.009

# Step 5 - Use CETAS

Create a parquet file based on creation of an external table from a user table

In [17]:
USE [WideWorldImporters];
GO
IF OBJECT_ID('wwi_customer_transactions', 'U') IS NOT NULL
	DROP EXTERNAL TABLE wwi_customer_transactions;
GO
CREATE EXTERNAL TABLE wwi_customer_transactions
WITH (
    LOCATION = '/wwi/',
    DATA_SOURCE = s3_wwi,  
    FILE_FORMAT = ParquetFileFormat
) 
AS
SELECT * FROM Sales.CustomerTransactions;
GO

Commands completed successfully.

Commands completed successfully.

(97147 rows affected)

Total execution time: 00:00:00.188

# Step 6 - Query external table

Run a query against the created external table to access parquet data. Join with a table in the database.

In [18]:
USE [WideWorldImporters];
GO
SELECT c.CustomerName, SUM(wct.OutstandingBalance) as total_balance
FROM wwi_customer_transactions wct
JOIN Sales.Customers c
ON wct.CustomerID = c.CustomerID
GROUP BY c.CustomerName
ORDER BY total_balance DESC;
GO

Commands completed successfully.

(263 rows affected)

Total execution time: 00:00:00.439

CustomerName total_balance Matyas Sedlar 0.00 Richard Friar 0.00 Eva Schulteisz 0.00 Tai Bach 0.00 Sumati Chatterjee 0.00 Victoria Lacusta 0.00 Gayatri Gajula 0.00 Isidora Morales 0.00 Pari Hosseini 0.00 Pinja Jantunen 0.00 Chandana Shasthri 0.00 Violetta KlanCisar 0.00 Volkan senturk 0.00 Dena Glissen 0.00 Sumati Bhat 0.00 Eugen Agafitei 0.00 Ajitaab Pakalapati 0.00 Sara Huiting 0.00 Olafs Rozitis 0.00 Bing Han 0.00 Kamila Michnova 0.00 Adrian Andreasson 0.00 Chin-Sun Chang 0.00 Gopalgobinda Sikdar 0.00 Allan Mannik 0.00 Leonardo Folliero 0.00 Gabriela Hernandes 0.00 Leyla Asef zade 0.00 Bahaar Asef zade 0.00 Sointu Savonheimo 0.00 Jai Lamble 0.00 Baran Jonsson 0.00 Debbie Molina 0.00 Chandrashekhar Dasgupta 0.00 Anindya Ghatak 0.00 Radha Barua 0.00 Maryann Huddleston 0.00 Magdalena Michnova 0.00 Edmee Glissen 0.00 Jitka Necesana 0.00 Miriam House 0.00 Leyla Siavashi 0.00 Marie LeBatelier 0.00 Philip Walker 0.00 Daniel Martensson 0.00 Hana Hlouskova 0.00 Katerina Hadrabova 0.00 Wingtip Toys (Head Office) 97053.58 Tailspin Toys (Head Office) 56435.84 Kumar Naicker 13212.12 Linh Dao 6728.65 Rodrigo Figueiredo 5975.40 Shyam Poddar 5767.83 Dominic Davignon 5732.98 Lilli Sokk 5689.31 Ana Florea 5511.15 Liidia Lepp 5422.25 Satish Mittal 5157.75 Isa Hulsegge 4713.85 Suparna Bhattacharya 4127.93 Narendra Tickoo 4038.80 Sabine Alksne 3876.65 Kertu Sokk 3545.22 Cosmina Vlad 3427.58 Marcela Lucescu 3276.35 Emma Van Zant 3091.20 Nils Kaulins 3034.85 Geza Roman 2685.25 Manca Hrastovsek 2217.33 Meera Patel 2157.40 Can ozcan 1910.73 Neil Farrelly 1834.25 Taneli Riutta 1517.08 Alena Kellnerova 1456.40 Lakshmi Benipal 1361.60 Baalaamjali Devulapalli 1361.60 Joel Carrillo 1223.60 Olya Izmaylov 745.20 Pavel Bogdanov 613.18 Crina Grasu 449.65 Elina Kaleja 426.08 Prabodh Nair 365.70 Luis Saucedo 325.45 Milinka Zujovic 235.75 Sabine Zalite 201.25 Tuulikki Linna 104.65 Melani Ravlen 0.00 Mauno Laurila 0.00 Om Yadav 0.00 Mahmut ozbek 0.00 Yves Belisle 0.00 Kamala Nishad 0.00 Roko Ilic 0.00 Akhil Nadar 0.00 Maksims Krastins 0.00 Andris Saulitis 0.00 Alinne Matos 0.00 Valter Viiding 0.00 Amarakumaar Gadiyaram 0.00 Emil Roman 0.00 Kumar Kamei 0.00 Dhanishta Mokkapati 0.00 Isidora Urias 0.00 Staffan Persson 0.00 Anca Gogean 0.00 Sara Walkky 0.00 Phoung Cu 0.00 Ingrida Zeltina 0.00 Be Trang 0.00 Bhagavati Vinjamuri 0.00 Rani Ganguly 0.00 Edgar Jogi 0.00 Dhaatri Chavva 0.00 Valentin Tirlea 0.00 Hee-Young Suh 0.00 Nhung Thach 0.00 Raghu Sandhu 0.00 Nasrin Omidzadeh 0.00 Chuan Wattanasin 0.00 Eliza Persson 0.00 Emily Whittle 0.00 Seo-yun Paik 0.00 Richard Zahradnicek 0.00 Svetlana Todorovic 0.00 David safranek 0.00 Hoc Tran 0.00 Ida Celma 0.00 Drazenka Jelic 0.00 Agrita Abele 0.00 Anand Mudaliyar 0.00 Jibek Juniskyzy 0.00 Jaroslav Fisar 0.00 Ganesh Majumdar 0.00 Kalyani Benjaree 0.00 Adriana Pena 0.00 Emma Salpa 0.00 Ian Olofsson 0.00 Sylvie Laramee 0.00 Amrita Ganguly 0.00 Amet Shergill 0.00 Abhra Ganguly 0.00 Ivana Hadrabova 0.00 Christian Couet 0.00 Matteo Cattaneo 0.00 Hanita Nookala 0.00 Raj Verma 0.00 Nguyen Banh 0.00 Tomo Vidovic 0.00 Damodar Shenoy 0.00 Bhaamini Palagummi 0.00 Damodara Trivedi 0.00 David Jaramillo 0.00 Erik Malk 0.00 Manjunatha Karnik 0.00 Aishwarya Dantuluri 0.00 Cuneyt Arslan 0.00 Som Mukherjee 0.00 Dipti Shah 0.00 Chompoo Atitarn 0.00 Veronika Necesana 0.00 Serdar ozden 0.00 Daniella Cavalcante 0.00 Arka Chatterjee 0.00 Farzana Habibi 0.00 Nadir Seddigh 0.00 Fabrice Cloutier 0.00 Hai Banh 0.00 Dhanishta Pullela 0.00 David Novacek 0.00 Aive Petrov 0.00 Annette Hetu 0.00 Urve Kasesalu 0.00 Rajeev Sandhu 0.00 Serdar ozCelik 0.00 Bhagavateeprasaad Malladi 0.00 Vedrana Kovacevic 0.00 Irma Berzina 0.00 Taj Syme 0.00 Bhadram Kamasamudram 0.00 Drishti Bose 0.00 Hue Ton 0.00 Stefan Selezeanu 0.00 Dinh Mai 0.00 Krishnam Allu 0.00 Kristi Part 0.00 Mahavir Sonkar 0.00 Nada Ana Slosar 0.00 Laszlo Gardenier 0.00 Libuse Kuchtova 0.00 Gasper Havzija 0.00 Darshana Madhunapantula 0.00 In-Su Bae 0.00 Abel Tatarescu 0.00 Laura Sykorova 0.00 Jasna Ce

# Step 7 - Use OPENROWSET() to query parquet files

Execute the following T-SQL to query parquet files stored in S3

In [19]:
USE [WideWorldImporters];
GO
SELECT *
FROM OPENROWSET
	(BULK '/wwi/'
	, FORMAT = 'PARQUET'
	, DATA_SOURCE = 's3_wwi')
as [wwi_customer_transactions_file];
GO

Commands completed successfully.

(97147 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:01.046

CustomerTransactionID CustomerID TransactionTypeID InvoiceID PaymentMethodID TransactionDate AmountExcludingTax TaxAmount TransactionAmount OutstandingBalance FinalizationDate IsFinalized LastEditedBy LastEditedWhen 2 832 1 1 NULL 2013-01-01 2300.00 345.00 2645.00 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 5 803 1 2 NULL 2013-01-01 405.00 60.75 465.75 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 7 1 1 3 NULL 2013-01-01 90.00 13.50 103.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 11 1 1 4 NULL 2013-01-01 445.20 66.78 511.98 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 15 905 1 5 NULL 2013-01-01 704.00 105.60 809.60 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 19 976 1 6 NULL 2013-01-01 430.00 64.50 494.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 24 401 1 7 NULL 2013-01-01 603.50 90.53 694.03 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 28 964 1 8 NULL 2013-01-01 258.00 38.70 296.70 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 31 1 1 9 NULL 2013-01-01 178.00 26.70 204.70 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 34 1 1 10 NULL 2013-01-01 104.00 15.60 119.60 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 36 401 1 11 NULL 2013-01-01 13.00 1.95 14.95 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 39 401 1 12 NULL 2013-01-01 229.00 34.35 263.35 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 42 401 1 13 NULL 2013-01-01 2430.00 364.50 2794.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 46 870 1 14 NULL 2013-01-01 650.00 97.50 747.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 49 991 1 15 NULL 2013-01-01 174.00 26.10 200.10 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 51 401 1 16 NULL 2013-01-01 68.00 10.20 78.20 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 54 910 1 17 NULL 2013-01-01 424.00 63.60 487.60 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 56 949 1 18 NULL 2013-01-01 91.00 13.65 104.65 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 60 973 1 19 NULL 2013-01-01 3185.00 477.75 3662.75 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 62 884 1 20 NULL 2013-01-01 240.00 36.00 276.00 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 66 1 1 21 NULL 2013-01-01 535.00 80.25 615.25 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 69 890 1 22 NULL 2013-01-01 3182.00 477.30 3659.30 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 73 1 1 23 NULL 2013-01-01 1490.00 223.50 1713.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 76 873 1 24 NULL 2013-01-01 472.00 70.80 542.80 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 79 401 1 25 NULL 2013-01-01 129.00 19.35 148.35 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 81 401 1 26 NULL 2013-01-01 13.00 1.95 14.95 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 84 1 1 27 NULL 2013-01-01 301.00 45.15 346.15 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 88 1 1 28 NULL 2013-01-01 4348.00 652.20 5000.20 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 91 972 1 29 NULL 2013-01-01 373.00 55.95 428.95 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 93 401 1 30 NULL 2013-01-01 100.00 15.00 115.00 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 97 1 1 31 NULL 2013-01-01 749.00 112.35 861.35 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 101 811 1 32 NULL 2013-01-01 780.00 117.00 897.00 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 103 1 1 33 NULL 2013-01-01 32.40 4.86 37.26 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 109 862 1 34 NULL 2013-01-01 823.00 123.45 946.45 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 111 401 1 35 NULL 2013-01-01 200.00 30.00 230.00 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 116 908 1 36 NULL 2013-01-01 482.00 72.30 554.30 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 118 995 1 37 NULL 2013-01-01 130.00 19.50 149.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 120 910 1 38 NULL 2013-01-01 26.00 3.90 29.90 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 124 401 1 39 NULL 2013-01-01 370.00 55.50 425.50 0.00 2013-01-02 1 10 2013-01-02 11:30:00.0000000 127 1000 1 40 NULL 

# Step 8 - Create an external table

Execute the following T-SQL to create an external table based on a parquet file with a subset of columns

In [20]:
USE [WideWorldImporters];
GO
IF OBJECT_ID('wwi_customer_transactions_base', 'U') IS NOT NULL
	DROP EXTERNAL TABLE wwi_customer_transactions_base;
GO
CREATE EXTERNAL TABLE wwi_customer_transactions_base 
( 
	CustomerTransactionID int, 
	CustomerID int,
	TransactionTypeID int,
	TransactionDate date,
	TransactionAmount decimal(18,2)
)
WITH 
(
	LOCATION = '/wwi/'
    , FILE_FORMAT = ParquetFileFormat
    , DATA_SOURCE = s3_wwi
);
GO
SELECT * FROM wwi_customer_transactions_base;
GO

Commands completed successfully.

Commands completed successfully.

Commands completed successfully.

(97147 rows affected)

Displaying Top 5000 rows.

Total execution time: 00:00:00.453

CustomerTransactionID CustomerID TransactionTypeID TransactionDate TransactionAmount 9183 401 3 2013-02-08 -35321.10 9184 810 3 2013-02-08 -2885.35 9185 821 3 2013-02-08 -6520.50 9186 822 3 2013-02-08 -616.40 9187 839 3 2013-02-08 -7423.25 9188 851 3 2013-02-08 -1449.00 9189 873 3 2013-02-08 -2178.10 9190 878 3 2013-02-08 -2663.40 9191 882 3 2013-02-08 -1607.70 9192 920 3 2013-02-08 -3220.00 9193 923 3 2013-02-08 -1214.40 9194 937 3 2013-02-08 -2288.50 9195 950 3 2013-02-08 -505.54 9196 992 3 2013-02-08 -2765.75 9199 1 1 2013-02-08 339.25 9203 1 1 2013-02-08 2079.20 9206 1 1 2013-02-08 2748.50 9211 1 1 2013-02-08 509.45 9214 1 1 2013-02-08 3542.00 9220 1 1 2013-02-08 2852.00 9226 1 1 2013-02-08 3384.45 9230 1 1 2013-02-08 896.77 9234 1 1 2013-02-08 12666.10 9239 1 1 2013-02-08 9363.30 9242 1 1 2013-02-08 975.20 9248 1 1 2013-02-08 1930.85 9252 1 1 2013-02-08 9226.16 9257 1 1 2013-02-08 5521.15 9263 1 1 2013-02-08 4417.15 9268 1 1 2013-02-08 2484.46 9270 1 1 2013-02-08 1738.80 9273 1 1 2013-02-08 372.60 9277 401 1 2013-02-08 3735.20 9282 401 1 2013-02-08 932.08 9287 401 1 2013-02-08 3413.20 9289 401 1 2013-02-08 248.40 9292 401 1 2013-02-08 1159.20 9297 401 1 2013-02-08 2130.95 9301 401 1 2013-02-08 3002.88 9305 401 1 2013-02-08 305.90 9308 401 1 2013-02-08 273.70 9311 401 1 2013-02-08 2321.85 9316 401 1 2013-02-08 1243.15 9321 401 1 2013-02-08 2523.10 9324 401 1 2013-02-08 2360.38 9330 401 1 2013-02-08 2831.30 9336 401 1 2013-02-08 7657.62 9342 401 1 2013-02-08 2722.34 9347 401 1 2013-02-08 2153.95 9352 806 1 2013-02-08 1329.40 9354 822 1 2013-02-08 496.80 9358 843 1 2013-02-08 332.93 9362 853 1 2013-02-08 2303.91 9366 862 1 2013-02-08 718.52 9369 866 1 2013-02-08 278.30 9372 876 1 2013-02-08 2989.08 9378 892 1 2013-02-08 11497.70 9381 899 1 2013-02-08 914.25 9387 901 1 2013-02-08 3397.10 9390 901 1 2013-02-08 1126.08 9396 907 1 2013-02-08 1225.33 9400 908 1 2013-02-08 297.56 9406 908 1 2013-02-08 7113.90 9412 930 1 2013-02-08 7726.39 9417 933 1 2013-02-08 8649.44 9422 938 1 2013-02-08 1687.05 9424 943 1 2013-02-08 1242.00 9427 953 1 2013-02-08 1127.00 9432 953 1 2013-02-08 2383.95 9438 962 1 2013-02-08 776.25 9443 962 1 2013-02-08 639.40 9448 971 1 2013-02-08 11600.06 9453 984 1 2013-02-08 4162.77 9454 1 3 2013-02-09 -65047.39 9455 401 3 2013-02-09 -39015.20 9456 806 3 2013-02-09 -1329.40 9457 822 3 2013-02-09 -496.80 9458 843 3 2013-02-09 -332.93 9459 853 3 2013-02-09 -2303.91 9460 862 3 2013-02-09 -718.52 9461 866 3 2013-02-09 -278.30 9462 876 3 2013-02-09 -2989.08 9463 892 3 2013-02-09 -11497.70 9464 899 3 2013-02-09 -914.25 9465 901 3 2013-02-09 -4523.18 9466 907 3 2013-02-09 -1225.33 9467 908 3 2013-02-09 -7411.46 9468 930 3 2013-02-09 -7726.39 9469 933 3 2013-02-09 -8649.44 9470 938 3 2013-02-09 -1687.05 9471 943 3 2013-02-09 -1242.00 9472 953 3 2013-02-09 -3510.95 9473 962 3 2013-02-09 -1415.65 9474 971 3 2013-02-09 -11600.06 9475 984 3 2013-02-09 -4162.77 9478 1 1 2013-02-09 11603.50 9481 1 1 2013-02-09 158.70 9486 1 1 2013-02-09 589.66 9491 1 1 2013-02-09 5064.60 9494 1 1 2013-02-09 4301.00 9499 1 1 2013-02-09 11892.84 9503 1 1 2013-02-09 2690.31 9509 1 1 2013-02-09 1140.46 9515 1 1 2013-02-09 4750.08 9520 1 1 2013-02-09 2817.56 9524 1 1 2013-02-09 2962.40 9530 1 1 2013-02-09 2248.25 9533 1 1 2013-02-09 641.13 9539 1 1 2013-02-09 1608.85 9545 1 1 2013-02-09 2995.75 9548 1 1 2013-02-09 571.55 9551 401 1 2013-02-09 12540.75 9556 401 1 2013-02-09 3946.23 9559 401 1 2013-02-09 2713.43 9563 401 1 2013-02-09 736.00 9566 401 1 2013-02-09 368.00 9570 401 1 2013-02-09 4654.05 9576 401 1 2013-02-09 5920.20 9582 401 1 2013-02-09 857.90 9585 401 1 2013-02-09 287.96 9591 401 1 2013-02-09 1691.65 9594 815 1 2013-02-09 533.60 9600 819 1 2013-02-09 1966.50 9604 820 1 2013-02-09 2823.25 9609 849 1 2013-02-09 4932.35 9612 854 1 2013-02-09 3070.50 9617 861 1 2013-02-09 961.46 9620 868 1 2013-02-09 1008.55 9625 876 1 2013-02-09 1581.77 9631 879 1 2013-02-09 3115.35 9635 879 1 2013-02-09 313.95 9639 888 1 2013-02-09 491.97 9643 944 1 201

# Step 9 - Create statistics on an external table

Execute the following T-SQL to create statistics on an external table

In [21]:
USE [WideWorldImporters];
GO
CREATE STATISTICS wwi_ctb_stats ON wwi_customer_transactions_base (CustomerID) WITH FULLSCAN;
GO

Commands completed successfully.

Commands completed successfully.

Total execution time: 00:00:00.383

# Step 10 - Explorer data virtualization metadata

Execute the following T-SQL statements to explore data virtualization metadata

In [22]:
USE [WideWorldImporters];
GO
SELECT * FROM sys.external_data_sources;
GO
SELECT * FROM sys.external_file_formats;
GO
SELECT * FROM sys.external_tables;
GO

Commands completed successfully.

(1 row affected)

(1 row affected)

(2 rows affected)

Total execution time: 00:00:00.094

data_source_id name location type_desc type resource_manager_location credential_id database_name shard_map_name connection_options pushdown 65536 s3_wwi s3://192.168.232.131:9000 NONE 6 NULL 65537 NULL NULL NULL ON

file_format_id name format_type field_terminator string_delimiter date_format use_type_default serde_method row_terminator encoding data_compression first_row parser_version 65536 ParquetFileFormat PARQUET NULL 0 NULL NULL NULL NULL NULL NULL

name object_id principal_id schema_id parent_object_id type type_desc create_date modify_date is_ms_shipped is_published is_schema_published max_column_id_used uses_ansi_nulls data_source_id file_format_id location reject_type reject_value reject_sample_value distribution_type distribution_desc sharding_col_id remote_schema_name remote_object_name rejected_row_location table_options partition_type partition_desc wwi_customer_transactions 1899153811 NULL 1 0 U USER_TABLE 2022-08-03 19:58:44.430 2022-08-03 19:58:44.430 0 0 0 14 1 65536 65536 /wwi/ VALUE 0 NULL NULL NULL NULL NULL NULL NULL NULL 0 NULL wwi_customer_transactions_base 1915153868 NULL 1 0 U USER_TABLE 2022-08-03 20:32:12.967 2022-08-03 20:32:12.967 0 0 0 5 1 65536 65536 /wwi/ VALUE 0 NULL NULL NULL NULL NULL NULL NULL NULL 0 NULL

# Step 11 - Explore parquet file metadata

Execute the following T-SQL statement to explore metadata about columns in the parquet file

In [23]:
USE [WideWorldImporters];
GO
EXEC sp_describe_first_result_set N'
SELECT *
FROM OPENROWSET
	(BULK ''/wwi/''
	, FORMAT = ''PARQUET''
	, DATA_SOURCE = ''s3_wwi'')
as [wwi_customer_transactions_file];';
GO

Commands completed successfully.

(14 rows affected)

Total execution time: 00:00:00.039

is_hidden column_ordinal name is_nullable system_type_id system_type_name max_length precision scale collation_name user_type_id user_type_database user_type_schema user_type_name assembly_qualified_type_name xml_collection_id xml_collection_database xml_collection_schema xml_collection_name is_xml_document is_case_sensitive is_fixed_length_clr_type source_server source_database source_schema source_table source_column is_identity_column is_part_of_unique_key is_updateable is_computed_column is_sparse_column_set ordinal_in_order_by_list order_by_is_descending order_by_list_length tds_type_id tds_length tds_collation_id tds_collation_sort_id 0 1 CustomerTransactionID 1 56 int 4 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 38 4 NULL NULL 0 2 CustomerID 1 56 int 4 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 38 4 NULL NULL 0 3 TransactionTypeID 1 56 int 4 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 38 4 NULL NULL 0 4 InvoiceID 1 56 int 4 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 38 4 NULL NULL 0 5 PaymentMethodID 1 56 int 4 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 38 4 NULL NULL 0 6 TransactionDate 1 40 date 3 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 40 3 NULL NULL 0 7 AmountExcludingTax 1 108 numeric(18,2) 9 18 2 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 108 17 NULL NULL 0 8 TaxAmount 1 108 numeric(18,2) 9 18 2 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 108 17 NULL NULL 0 9 TransactionAmount 1 108 numeric(18,2) 9 18 2 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 108 17 NULL NULL 0 10 OutstandingBalance 1 108 numeric(18,2) 9 18 2 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 108 17 NULL NULL 0 11 FinalizationDate 1 40 date 3 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 40 3 NULL NULL 0 12 IsFinalized 1 104 bit 1 1 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 104 1 NULL NULL 0 13 LastEditedBy 1 56 int 4 10 0 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 38 4 NULL NULL 0 14 LastEditedWhen 1 42 datetime2(7) 8 27 7 NULL NULL NULL NULL NULL NULL NULL NULL NULL NULL 0 0 0 NULL NULL NULL NULL NULL 0 NULL 1 0 0 NULL NULL NULL 42 8 NULL NULL

# Step 12 - Explore file metadata

Execute the following T-SQL statement to explore metadata from the external table about the source parquet files

In [24]:
USE [WideWorldImporters];
GO
SELECT TOP 1 wwi_customer_transactions_file.filepath(), 
wwi_customer_transactions_file.filename()
FROM OPENROWSET
	(BULK '/wwi/'
	, FORMAT = 'PARQUET'
	, DATA_SOURCE = 's3_wwi')
as [wwi_customer_transactions_file];
GO

Commands completed successfully.

(1 row affected)

Total execution time: 00:00:00.033

(No column name) (No column name) s3://192.168.232.131:9000/wwi/4E605C68-A1C5-4C42-B1E8-B935C448347F-1-1.parquet 4E605C68-A1C5-4C42-B1E8-B935C448347F-1-1.parquet